In [1]:
import numpy as np
import pandas as pd
from numpy import array
import matplotlib.pyplot as plt

from sklearn.feature_selection import f_classif, mutual_info_classif, SelectFdr

from sklearn.feature_selection import GenericUnivariateSelect
from sklearn.svm import LinearSVC, NuSVC
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier 

from scipy.stats import uniform, randint

import numpy as np
import matplotlib.pyplot as plt
from sklearn.naive_bayes import GaussianNB
from sklearn.svm import SVC
from sklearn.datasets import load_digits
from sklearn.model_selection import learning_curve
from sklearn.model_selection import ShuffleSplit
from sklearn.model_selection import cross_val_score

import xgboost as xgb
from sklearn.metrics import auc, accuracy_score, confusion_matrix, mean_squared_error
from sklearn.model_selection import cross_val_score, GridSearchCV, KFold, RandomizedSearchCV, train_test_split

from warnings import filterwarnings
filterwarnings('ignore')


In [2]:

def plot_learning_curve(estimator, title, X, y, axes=None, ylim=None, cv=None,
                        n_jobs=None, train_sizes=np.linspace(.1, 1.0, 5)):
    """
    Generate 3 plots: the test and training learning curve, the training
    samples vs fit times curve, the fit times vs score curve.

    Parameters
    ----------
    estimator : object type that implements the "fit" and "predict" methods
        An object of that type which is cloned for each validation.

    title : string
        Title for the chart.

    X : array-like, shape (n_samples, n_features)
        Training vector, where n_samples is the number of samples and
        n_features is the number of features.

    y : array-like, shape (n_samples) or (n_samples, n_features), optional
        Target relative to X for classification or regression;
        None for unsupervised learning.

    axes : array of 3 axes, optional (default=None)
        Axes to use for plotting the curves.

    ylim : tuple, shape (ymin, ymax), optional
        Defines minimum and maximum yvalues plotted.

    cv : int, cross-validation generator or an iterable, optional
        Determines the cross-validation splitting strategy.
        Possible inputs for cv are:

          - None, to use the default 5-fold cross-validation,
          - integer, to specify the number of folds.
          - :term:`CV splitter`,
          - An iterable yielding (train, test) splits as arrays of indices.

        For integer/None inputs, if ``y`` is binary or multiclass,
        :class:`StratifiedKFold` used. If the estimator is not a classifier
        or if ``y`` is neither binary nor multiclass, :class:`KFold` is used.

        Refer :ref:`User Guide <cross_validation>` for the various
        cross-validators that can be used here.

    n_jobs : int or None, optional (default=None)
        Number of jobs to run in parallel.
        ``None`` means 1 unless in a :obj:`joblib.parallel_backend` context.
        ``-1`` means using all processors. See :term:`Glossary <n_jobs>`
        for more details.

    train_sizes : array-like, shape (n_ticks,), dtype float or int
        Relative or absolute numbers of training examples that will be used to
        generate the learning curve. If the dtype is float, it is regarded as a
        fraction of the maximum size of the training set (that is determined
        by the selected validation method), i.e. it has to be within (0, 1].
        Otherwise it is interpreted as absolute sizes of the training sets.
        Note that for classification the number of samples usually have to
        be big enough to contain at least one sample from each class.
        (default: np.linspace(0.1, 1.0, 5))
    """
    if axes is None:
        _, axes = plt.subplots(1, 3, figsize=(20, 5))

    axes[0].set_title(title)
    if ylim is not None:
        axes[0].set_ylim(*ylim)
    axes[0].set_xlabel("Training examples")
    axes[0].set_ylabel("Score")

    train_sizes, train_scores, test_scores, fit_times, _ = \
        learning_curve(estimator, X, y, cv=cv, n_jobs=n_jobs,
                       train_sizes=train_sizes,
                       return_times=True)
    train_scores_mean = np.mean(train_scores, axis=1)
    train_scores_std = np.std(train_scores, axis=1)
    test_scores_mean = np.mean(test_scores, axis=1)
    test_scores_std = np.std(test_scores, axis=1)
    fit_times_mean = np.mean(fit_times, axis=1)
    fit_times_std = np.std(fit_times, axis=1)

    # Plot learning curve
    axes[0].grid()
    axes[0].fill_between(train_sizes, train_scores_mean - train_scores_std,
                         train_scores_mean + train_scores_std, alpha=0.1,
                         color="r")
    axes[0].fill_between(train_sizes, test_scores_mean - test_scores_std,
                         test_scores_mean + test_scores_std, alpha=0.1,
                         color="g")
    axes[0].plot(train_sizes, train_scores_mean, 'o-', color="r",
                 label="Training score")
    axes[0].plot(train_sizes, test_scores_mean, 'o-', color="g",
                 label="Cross-validation score")
    axes[0].legend(loc="best")

    # Plot n_samples vs fit_times
    axes[1].grid()
    axes[1].plot(train_sizes, fit_times_mean, 'o-')
    axes[1].fill_between(train_sizes, fit_times_mean - fit_times_std,
                         fit_times_mean + fit_times_std, alpha=0.1)
    axes[1].set_xlabel("Training examples")
    axes[1].set_ylabel("fit_times")
    axes[1].set_title("Scalability of the model")

    # Plot fit_time vs score
    axes[2].grid()
    axes[2].plot(fit_times_mean, test_scores_mean, 'o-')
    axes[2].fill_between(fit_times_mean, test_scores_mean - test_scores_std,
                         test_scores_mean + test_scores_std, alpha=0.1)
    axes[2].set_xlabel("fit_times")
    axes[2].set_ylabel("Score")
    axes[2].set_title("Performance of the model")

    return plt

In [9]:
def hyper_opt_procedure(model_object,params,cv,perf_df,X,y):


  model = model_object()

  # Initial Model Fit with stock hyper_params

  init_score = np.mean(cross_val_score(model,X,y,cv=cv))

  perf_df = perf_df.append({'Model Iteration': 'Stock Params',
                              'Score':init_score}, ignore_index=True)

  print('Initial Model with Stock Params Score : {}'.format(init_score))

  # Random Search Cross Validation


  search_model = RandomizedSearchCV(model,
                                         param_distributions=params,
                                         random_state=42, 
                                         n_iter=300, 
                                         cv=cv, 
                                         verbose=1, 
                                         n_jobs=1, 
                                         return_train_score=True)

  search_model.fit(X,y)

  best_search_model = search_model.best_estimator_

  best_search_model_score = search_model.best_score_

  perf_df = perf_df.append({'Model Iteration': 'Random HP Search Best Model',
                      'Score':best_search_model_score}, ignore_index=True)

  rd_score_improv = ((best_search_model_score - init_score)/init_score) * 100

  print('Random HP Search Best Model Score : {}'.format(best_search_model_score))

  print('Improvement of {}% relative to the initial model'.format(rd_score_improv))
  
  


  return model, best_search_model
   



class hyper_model:
    
    def __init__(self,model_name,validation_approach,X,y):
        
        self.model_name = model_name
        self.X = X
        self.y = y
        self.validation_approach= validation_approach
        self.best_model = None
        self.best_params = None
        self.all_models_perf = pd.DataFrame(None,columns=['Model Iteration','Score'])
        self.stock_model = None
        self.rd_model = None


    def fit(self):


      if self.validation_approach == 'leave-one-run-out':

        cv = KFold(n_splits=8, shuffle=False)

      elif self.validation_approach == 'leave-one-run-out-shuffled':

        cv = KFold(n_splits=8, shuffle=True, random_state=42)

      elif self.validation_approach == 'leave-one-task-out':

        cv = KFold(n_splits=4, shuffle=False)

      elif self.validation_approach == 'leave-one-task-out-shuffled':

        cv = KFold(n_splits=4, shuffle=True, random_state=42)    


 
        
        # Linear SVM

      if self.model_name == 'linear_svm':

        params = {'C': [0.1, 1, 10, 100, 1000]} 

        self.stock_model, self.rd_model = hyper_opt_procedure(model_object=LinearSVC,
                                                                                                 params=params,cv=cv,
                                                                                                 perf_df=self.all_models_perf,
                                                                                                 X=self.X,y=self.y)

         

      # Non Linear SVM


      elif self.model_name == 'non_linear_svm':

        params = {'nu': [0.01, 0.3, 0.5, 0.7, 1],  
                        'gamma': [1, 0.1, 0.01, 0.001, 0.0001], 
                        'kernel': ['rbf','poly','sigmoid']
                       }


        self.stock_model, self.rd_model = hyper_opt_procedure(model_object=NuSVC,
                                                                                                 params=params,cv=cv,
                                                                                                 perf_df=self.all_models_perf,
                                                                                                 X=self.X,y=self.y)

          
      # Random Forest Classifier


      elif self.model_name == 'random_forest_classifier':


        params = {'bootstrap': [True],
                    'max_depth': [60],
                    'max_features': ['auto'],
                    'min_samples_leaf': [4],
                    'min_samples_split': [2, 5],
                    'n_estimators': [1000]
                   }


        self.stock_model, self.rd_model = hyper_opt_procedure(model_object=RandomForestClassifier,
                                                                                                 params=params,cv=cv,
                                                                                                 perf_df=self.all_models_perf,
                                                                                                 X=self.X,y=self.y)
          



      # XG Boost Classifier


      elif self.model_name == 'xg_boost':

        params = {
              "colsample_bytree": uniform(0.7, 0.3),
              "gamma": uniform(0, 0.5),
              "learning_rate": uniform(0.03, 0.3), 
              "max_depth": randint(2, 6), 
              "n_estimators": randint(100, 150),
              "subsample": uniform(0.6, 0.4)
              }

        self.stock_model, self.rd_model = hyper_opt_procedure(model_object=xgb.XGBClassifier,
                                                                                                 params=params,cv=cv,
                                                                                                 perf_df=self.all_models_perf,
                                                                                                 X=self.X,y=self.y)  

                
                

In [10]:
X = np.load('../../data/X_pref_lss_shift_linear_vmpfc.npy')

In [11]:
X.shape

(480, 3)

In [12]:
y = np.load('../../data/y_pref_lss_shift_linear_vmpfc.npy')

In [13]:
y.shape

(480, 1)

## Features Selection

### Filter

No FS needed, only 3 needeed

### Data Preparation

In [14]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.10, random_state=42)

## Linear Support Vector Machine

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [15]:
hm_linear_svm_to = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [16]:
hm_linear_svm_to.fit()

Initial Model with Stock Params Score : 0.4166666666666667
Fitting 4 folds for each of 5 candidates, totalling 20 fits
Random HP Search Best Model Score : 0.4708333333333333
Improvement of 12.999999999999993% relative to the initial model


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    0.0s finished


In [17]:
hm_linear_svm_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [18]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [19]:
scores

array([0.55833333, 0.36666667, 0.50833333, 0.23333333])

In [20]:
mean_score

0.4166666666666667

In [21]:
# leave-one-task-out-shuffled test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [22]:
scores

array([0.51666667, 0.49166667, 0.525     , 0.53333333])

In [23]:
mean_score

0.5166666666666666

In [24]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [25]:
scores

array([0.63333333, 0.48333333, 0.35      , 0.38333333, 0.5       ,
       0.51666667, 0.8       , 0.73333333])

In [26]:
mean_score

0.55

In [27]:
# leave-one-run-out-shuffled test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [28]:
scores

array([0.55      , 0.48333333, 0.43333333, 0.56666667, 0.63333333,
       0.58333333, 0.53333333, 0.53333333])

In [29]:
mean_score

0.5395833333333333

In [30]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [31]:
hm_linear_svm_tos = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [32]:
hm_linear_svm_tos.fit()

Initial Model with Stock Params Score : 0.5166666666666666
Fitting 4 folds for each of 5 candidates, totalling 20 fits
Random HP Search Best Model Score : 0.525
Improvement of 1.6129032258064675% relative to the initial model


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    0.0s finished


In [33]:
hm_linear_svm_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [34]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [35]:
scores

array([0.55833333, 0.36666667, 0.50833333, 0.23333333])

In [36]:
mean_score

0.4166666666666667

In [37]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [38]:
scores

array([0.51666667, 0.49166667, 0.525     , 0.53333333])

In [39]:
mean_score

0.5166666666666666

In [40]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [41]:
scores

array([0.63333333, 0.48333333, 0.35      , 0.38333333, 0.5       ,
       0.51666667, 0.8       , 0.73333333])

In [42]:
mean_score

0.55

In [43]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [44]:
scores

array([0.55      , 0.48333333, 0.43333333, 0.56666667, 0.63333333,
       0.58333333, 0.53333333, 0.53333333])

In [45]:
mean_score

0.5395833333333333

In [46]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [47]:
hm_linear_svm_ro = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [48]:
hm_linear_svm_ro.fit()

Initial Model with Stock Params Score : 0.55
Fitting 8 folds for each of 5 candidates, totalling 40 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5520833333333334
Improvement of 0.3787878787878774% relative to the initial model


[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:    0.2s finished


In [49]:
hm_linear_svm_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [50]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [51]:
scores

array([0.55833333, 0.36666667, 0.50833333, 0.23333333])

In [52]:
mean_score

0.4166666666666667

In [53]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [54]:
scores

array([0.51666667, 0.49166667, 0.525     , 0.53333333])

In [55]:
mean_score

0.5166666666666666

In [56]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [57]:
scores

array([0.63333333, 0.48333333, 0.35      , 0.38333333, 0.5       ,
       0.51666667, 0.8       , 0.73333333])

In [58]:
mean_score

0.55

In [59]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [60]:
scores

array([0.55      , 0.48333333, 0.43333333, 0.56666667, 0.63333333,
       0.58333333, 0.53333333, 0.53333333])

In [61]:
mean_score

0.5395833333333333

In [62]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [63]:
hm_linear_svm_ros = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [64]:
hm_linear_svm_ros.fit()

Initial Model with Stock Params Score : 0.5395833333333333
Fitting 8 folds for each of 5 candidates, totalling 40 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5416666666666666
Improvement of 0.3861003861003848% relative to the initial model


[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:    0.2s finished


In [65]:
hm_linear_svm_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [66]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [67]:
scores

array([0.55833333, 0.36666667, 0.50833333, 0.23333333])

In [68]:
mean_score

0.4166666666666667

In [69]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [70]:
scores

array([0.51666667, 0.49166667, 0.525     , 0.53333333])

In [71]:
mean_score

0.5166666666666666

In [72]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [73]:
scores

array([0.63333333, 0.48333333, 0.35      , 0.38333333, 0.5       ,
       0.51666667, 0.8       , 0.73333333])

In [74]:
mean_score

0.55

In [75]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [76]:
scores

array([0.55      , 0.48333333, 0.43333333, 0.56666667, 0.63333333,
       0.58333333, 0.53333333, 0.53333333])

In [77]:
mean_score

0.5395833333333333

In [78]:
# other metrics + graphs




### Hyper_optimized model

#### *leave-one-task-out* cross validation

##### Training

In [79]:
hm_linear_svm_to = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [80]:
hm_linear_svm_to.fit()

Initial Model with Stock Params Score : 0.4166666666666667
Fitting 4 folds for each of 5 candidates, totalling 20 fits
Random HP Search Best Model Score : 0.5416666666666667
Improvement of 30.00000000000001% relative to the initial model


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    0.0s finished


In [81]:
hm_linear_svm_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [82]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [83]:
scores

array([0.51666667, 0.45833333, 0.45      , 0.51666667])

In [84]:
mean_score

0.4854166666666667

In [85]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [86]:
scores

array([0.45      , 0.46666667, 0.53333333, 0.45      ])

In [87]:
mean_score

0.47500000000000003

In [88]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [89]:
scores

array([0.53333333, 0.55      , 0.5       , 0.38333333, 0.53333333,
       0.55      , 0.48333333, 0.4       ])

In [90]:
mean_score

0.4916666666666667

In [91]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [92]:
scores

array([0.5       , 0.4       , 0.36666667, 0.51666667, 0.61666667,
       0.61666667, 0.48333333, 0.38333333])

In [93]:
mean_score

0.48541666666666666

In [94]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [95]:
hm_linear_svm_tos = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [96]:
hm_linear_svm_tos.fit()

Initial Model with Stock Params Score : 0.5166666666666666
Fitting 4 folds for each of 5 candidates, totalling 20 fits
Random HP Search Best Model Score : 0.525
Improvement of 1.6129032258064675% relative to the initial model


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done  20 out of  20 | elapsed:    0.0s finished


In [97]:
hm_linear_svm_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [98]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [99]:
scores

array([0.55833333, 0.36666667, 0.50833333, 0.23333333])

In [100]:
mean_score

0.4166666666666667

In [101]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [102]:
scores

array([0.51666667, 0.5       , 0.55      , 0.53333333])

In [103]:
mean_score

0.525

In [104]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [105]:
scores

array([0.63333333, 0.48333333, 0.35      , 0.38333333, 0.5       ,
       0.51666667, 0.8       , 0.73333333])

In [106]:
mean_score

0.55

In [107]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [108]:
scores

array([0.55      , 0.48333333, 0.45      , 0.56666667, 0.63333333,
       0.58333333, 0.53333333, 0.53333333])

In [109]:
mean_score

0.5416666666666666

In [110]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [111]:
hm_linear_svm_ro = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [112]:
hm_linear_svm_ro.fit()

Initial Model with Stock Params Score : 0.55
Fitting 8 folds for each of 5 candidates, totalling 40 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.55
Improvement of 0.0% relative to the initial model


[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:    0.2s finished


In [113]:
hm_linear_svm_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [114]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [115]:
scores

array([0.55833333, 0.36666667, 0.50833333, 0.23333333])

In [116]:
mean_score

0.4166666666666667

In [117]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [118]:
scores

array([0.51666667, 0.5       , 0.55      , 0.53333333])

In [119]:
mean_score

0.525

In [120]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [121]:
scores

array([0.63333333, 0.48333333, 0.35      , 0.38333333, 0.5       ,
       0.51666667, 0.8       , 0.73333333])

In [122]:
mean_score

0.55

In [123]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [124]:
scores

array([0.55      , 0.48333333, 0.45      , 0.56666667, 0.63333333,
       0.58333333, 0.53333333, 0.53333333])

In [125]:
mean_score

0.5416666666666666

In [126]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [127]:
hm_linear_svm_ros = hyper_model(model_name='linear_svm',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [128]:
hm_linear_svm_ros.fit()

Initial Model with Stock Params Score : 0.5395833333333333
Fitting 8 folds for each of 5 candidates, totalling 40 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5416666666666666
Improvement of 0.3861003861003848% relative to the initial model


[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:    0.2s finished


In [129]:
hm_linear_svm_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [130]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [131]:
scores

array([0.55833333, 0.36666667, 0.50833333, 0.23333333])

In [132]:
mean_score

0.4166666666666667

In [133]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [134]:
scores

array([0.51666667, 0.5       , 0.55      , 0.53333333])

In [135]:
mean_score

0.525

In [136]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [137]:
scores

array([0.63333333, 0.48333333, 0.35      , 0.38333333, 0.5       ,
       0.51666667, 0.8       , 0.73333333])

In [138]:
mean_score

0.55

In [139]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [140]:
scores

array([0.55      , 0.48333333, 0.45      , 0.56666667, 0.63333333,
       0.58333333, 0.53333333, 0.53333333])

In [141]:
mean_score

0.5416666666666666

In [142]:
# other metrics + graphs




## Non Linear Support Vector Machine

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [143]:
hm_non_linear_svm_to = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [144]:
hm_non_linear_svm_to.fit()

Initial Model with Stock Params Score : 0.5479166666666666
Fitting 4 folds for each of 75 candidates, totalling 300 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.6166666666666667
Improvement of 12.547528517110285% relative to the initial model


[Parallel(n_jobs=1)]: Done 300 out of 300 | elapsed:  1.6min finished


In [145]:
hm_non_linear_svm_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [146]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [147]:
scores

array([0.525     , 0.6       , 0.50833333, 0.55833333])

In [148]:
mean_score

0.5479166666666666

In [149]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [150]:
scores

array([0.475     , 0.51666667, 0.55833333, 0.525     ])

In [151]:
mean_score

0.51875

In [152]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [153]:
scores

array([0.51666667, 0.46666667, 0.56666667, 0.41666667, 0.41666667,
       0.46666667, 0.56666667, 0.45      ])

In [154]:
mean_score

0.48333333333333334

In [155]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [156]:
scores

array([0.51666667, 0.53333333, 0.58333333, 0.43333333, 0.46666667,
       0.55      , 0.58333333, 0.63333333])

In [157]:
mean_score

0.5375

In [158]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [159]:
hm_non_linear_svm_tos = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [160]:
hm_non_linear_svm_tos.fit()

Initial Model with Stock Params Score : 0.51875
Fitting 4 folds for each of 75 candidates, totalling 300 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5666666666666667
Improvement of 9.236947791164646% relative to the initial model


[Parallel(n_jobs=1)]: Done 300 out of 300 | elapsed:  1.9min finished


In [161]:
hm_non_linear_svm_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [162]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [163]:
scores

array([0.525     , 0.6       , 0.50833333, 0.55833333])

In [164]:
mean_score

0.5479166666666666

In [165]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [166]:
scores

array([0.475     , 0.51666667, 0.55833333, 0.525     ])

In [167]:
mean_score

0.51875

In [168]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [169]:
scores

array([0.51666667, 0.46666667, 0.56666667, 0.41666667, 0.41666667,
       0.46666667, 0.56666667, 0.45      ])

In [170]:
mean_score

0.48333333333333334

In [171]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [172]:
scores

array([0.51666667, 0.53333333, 0.58333333, 0.43333333, 0.46666667,
       0.55      , 0.58333333, 0.63333333])

In [173]:
mean_score

0.5375

In [174]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [175]:
hm_non_linear_svm_ro = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [176]:
hm_non_linear_svm_ro.fit()

Initial Model with Stock Params Score : 0.48333333333333334
Fitting 8 folds for each of 75 candidates, totalling 600 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5770833333333334
Improvement of 19.396551724137943% relative to the initial model


[Parallel(n_jobs=1)]: Done 600 out of 600 | elapsed:  7.4min finished


In [177]:
hm_non_linear_svm_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [178]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [179]:
scores

array([0.525     , 0.6       , 0.50833333, 0.55833333])

In [180]:
mean_score

0.5479166666666666

In [181]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [182]:
scores

array([0.475     , 0.51666667, 0.55833333, 0.525     ])

In [183]:
mean_score

0.51875

In [184]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [185]:
scores

array([0.51666667, 0.46666667, 0.56666667, 0.41666667, 0.41666667,
       0.46666667, 0.56666667, 0.45      ])

In [186]:
mean_score

0.48333333333333334

In [187]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [188]:
scores

array([0.51666667, 0.53333333, 0.58333333, 0.43333333, 0.46666667,
       0.55      , 0.58333333, 0.63333333])

In [189]:
mean_score

0.5375

In [190]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [191]:
hm_non_linear_svm_ros = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [192]:
hm_non_linear_svm_ros.fit()

Initial Model with Stock Params Score : 0.5375
Fitting 8 folds for each of 75 candidates, totalling 600 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5645833333333333
Improvement of 5.038759689922483% relative to the initial model


[Parallel(n_jobs=1)]: Done 600 out of 600 | elapsed:  3.3min finished


In [193]:
hm_non_linear_svm_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [194]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [195]:
scores

array([0.525     , 0.6       , 0.50833333, 0.55833333])

In [196]:
mean_score

0.5479166666666666

In [197]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [198]:
scores

array([0.475     , 0.51666667, 0.55833333, 0.525     ])

In [199]:
mean_score

0.51875

In [200]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [201]:
scores

array([0.51666667, 0.46666667, 0.56666667, 0.41666667, 0.41666667,
       0.46666667, 0.56666667, 0.45      ])

In [202]:
mean_score

0.48333333333333334

In [203]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [204]:
scores

array([0.51666667, 0.53333333, 0.58333333, 0.43333333, 0.46666667,
       0.55      , 0.58333333, 0.63333333])

In [205]:
mean_score

0.5375

In [206]:
# other metrics + graphs




### Hyper_optimized model

#### *leave-one-task-out* cross validation

##### Training

In [207]:
hm_non_linear_svm_to = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [208]:
hm_non_linear_svm_to.fit()

Initial Model with Stock Params Score : 0.5479166666666666
Fitting 4 folds for each of 75 candidates, totalling 300 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.6166666666666667
Improvement of 12.547528517110285% relative to the initial model


[Parallel(n_jobs=1)]: Done 300 out of 300 | elapsed:  1.5min finished


In [209]:
hm_non_linear_svm_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [210]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [211]:
scores

array([0.59166667, 0.65833333, 0.55      , 0.66666667])

In [212]:
mean_score

0.6166666666666667

In [213]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [214]:
scores

array([0.54166667, 0.5       , 0.525     , 0.56666667])

In [215]:
mean_score

0.5333333333333332

In [216]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [217]:
scores

array([0.43333333, 0.53333333, 0.65      , 0.46666667, 0.5       ,
       0.48333333, 0.66666667, 0.61666667])

In [218]:
mean_score

0.54375

In [219]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [220]:
scores

array([0.51666667, 0.46666667, 0.4       , 0.48333333, 0.53333333,
       0.35      , 0.51666667, 0.53333333])

In [221]:
mean_score

0.475

In [222]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [223]:
hm_non_linear_svm_tos = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [224]:
hm_non_linear_svm_tos.fit()

Initial Model with Stock Params Score : 0.51875
Fitting 4 folds for each of 75 candidates, totalling 300 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5666666666666667
Improvement of 9.236947791164646% relative to the initial model


[Parallel(n_jobs=1)]: Done 300 out of 300 | elapsed:  1.7min finished


In [225]:
hm_non_linear_svm_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [226]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [227]:
scores

array([0.5       , 0.54166667, 0.53333333, 0.51666667])

In [228]:
mean_score

0.5229166666666666

In [229]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [230]:
scores

array([0.58333333, 0.575     , 0.53333333, 0.575     ])

In [231]:
mean_score

0.5666666666666667

In [232]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [233]:
scores

array([0.5       , 0.45      , 0.56666667, 0.51666667, 0.5       ,
       0.46666667, 0.51666667, 0.48333333])

In [234]:
mean_score

0.5

In [235]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [236]:
scores

array([0.53333333, 0.63333333, 0.55      , 0.58333333, 0.6       ,
       0.48333333, 0.5       , 0.63333333])

In [237]:
mean_score

0.5645833333333333

In [238]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [239]:
hm_non_linear_svm_ro = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [240]:
hm_non_linear_svm_ro.fit()

Initial Model with Stock Params Score : 0.48333333333333334
Fitting 8 folds for each of 75 candidates, totalling 600 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5770833333333334
Improvement of 19.396551724137943% relative to the initial model


[Parallel(n_jobs=1)]: Done 600 out of 600 | elapsed:  8.2min finished


In [241]:
hm_non_linear_svm_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [242]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [243]:
scores

array([0.51666667, 0.59166667, 0.5       , 0.25833333])

In [244]:
mean_score

0.4666666666666667

In [245]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [246]:
scores

array([0.5       , 0.54166667, 0.59166667, 0.525     ])

In [247]:
mean_score

0.5395833333333333

In [248]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [249]:
scores

array([0.63333333, 0.5       , 0.61666667, 0.4       , 0.5       ,
       0.51666667, 0.76666667, 0.68333333])

In [250]:
mean_score

0.5770833333333334

In [251]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [252]:
scores

array([0.48333333, 0.5       , 0.41666667, 0.45      , 0.63333333,
       0.45      , 0.46666667, 0.53333333])

In [253]:
mean_score

0.49166666666666664

In [254]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [255]:
hm_non_linear_svm_ros = hyper_model(model_name='non_linear_svm',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [256]:
hm_non_linear_svm_ros.fit()

Initial Model with Stock Params Score : 0.5375
Fitting 8 folds for each of 75 candidates, totalling 600 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Random HP Search Best Model Score : 0.5645833333333333
Improvement of 5.038759689922483% relative to the initial model


[Parallel(n_jobs=1)]: Done 600 out of 600 | elapsed:  3.7min finished


In [257]:
hm_non_linear_svm_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [258]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [259]:
scores

array([0.5       , 0.54166667, 0.53333333, 0.51666667])

In [260]:
mean_score

0.5229166666666666

In [261]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [262]:
scores

array([0.58333333, 0.575     , 0.53333333, 0.575     ])

In [263]:
mean_score

0.5666666666666667

In [264]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_non_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [265]:
scores

array([0.5       , 0.45      , 0.56666667, 0.51666667, 0.5       ,
       0.46666667, 0.51666667, 0.48333333])

In [266]:
mean_score

0.5

In [267]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_non_linear_svm_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [268]:
scores

array([0.53333333, 0.63333333, 0.55      , 0.58333333, 0.6       ,
       0.48333333, 0.5       , 0.63333333])

In [269]:
mean_score

0.5645833333333333

In [270]:
# other metrics + graphs




## Random Forest Classifier

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [271]:
hm_rf_to = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [272]:
hm_rf_to.fit()

Initial Model with Stock Params Score : 0.5145833333333334
Fitting 4 folds for each of 300 candidates, totalling 1200 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed: 30.5min finished


Random HP Search Best Model Score : 0.5375
Improvement of 4.4534412955465426% relative to the initial model


In [273]:
hm_rf_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [274]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [275]:
scores

array([0.56666667, 0.50833333, 0.575     , 0.48333333])

In [276]:
mean_score

0.5333333333333333

In [277]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [278]:
scores

array([0.55833333, 0.53333333, 0.55      , 0.55833333])

In [279]:
mean_score

0.55

In [280]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [281]:
scores

array([0.48333333, 0.48333333, 0.5       , 0.51666667, 0.53333333,
       0.53333333, 0.41666667, 0.43333333])

In [282]:
mean_score

0.48750000000000004

In [283]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [284]:
scores

array([0.5       , 0.51666667, 0.5       , 0.5       , 0.58333333,
       0.43333333, 0.5       , 0.58333333])

In [285]:
mean_score

0.5145833333333334

In [286]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [287]:
hm_rf_tos = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [288]:
hm_rf_tos.fit()

Initial Model with Stock Params Score : 0.5333333333333333
Fitting 4 folds for each of 300 candidates, totalling 1200 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed: 29.3min finished


Random HP Search Best Model Score : 0.5854166666666667
Improvement of 9.765625000000007% relative to the initial model


In [289]:
hm_rf_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [290]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [291]:
scores

array([0.55      , 0.51666667, 0.575     , 0.475     ])

In [292]:
mean_score

0.5291666666666667

In [293]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [294]:
scores

array([0.56666667, 0.575     , 0.54166667, 0.58333333])

In [295]:
mean_score

0.5666666666666667

In [296]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [297]:
scores

array([0.48333333, 0.48333333, 0.45      , 0.56666667, 0.61666667,
       0.58333333, 0.5       , 0.41666667])

In [298]:
mean_score

0.5125000000000001

In [299]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [300]:
scores

array([0.45      , 0.56666667, 0.5       , 0.53333333, 0.61666667,
       0.36666667, 0.56666667, 0.6       ])

In [301]:
mean_score

0.5249999999999999

In [302]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [303]:
hm_rf_ro = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [304]:
hm_rf_ro.fit()

Initial Model with Stock Params Score : 0.5208333333333333
Fitting 8 folds for each of 300 candidates, totalling 2400 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed: 82.8min finished


Random HP Search Best Model Score : 0.5375000000000001
Improvement of 3.200000000000032% relative to the initial model


In [305]:
hm_rf_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [306]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [307]:
scores

array([0.55      , 0.48333333, 0.58333333, 0.44166667])

In [308]:
mean_score

0.5145833333333334

In [309]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [310]:
scores

array([0.54166667, 0.54166667, 0.51666667, 0.58333333])

In [311]:
mean_score

0.5458333333333334

In [312]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [313]:
scores

array([0.46666667, 0.45      , 0.46666667, 0.53333333, 0.55      ,
       0.55      , 0.46666667, 0.5       ])

In [314]:
mean_score

0.4979166666666667

In [315]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [316]:
scores

array([0.53333333, 0.56666667, 0.48333333, 0.51666667, 0.6       ,
       0.36666667, 0.53333333, 0.6       ])

In [317]:
mean_score

0.5249999999999999

In [318]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [319]:
hm_rf_ros = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [320]:
hm_rf_ros.fit()

Initial Model with Stock Params Score : 0.51875
Fitting 8 folds for each of 300 candidates, totalling 2400 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed: 106.0min finished


Random HP Search Best Model Score : 0.5541666666666667
Improvement of 6.827309236947787% relative to the initial model


In [321]:
hm_rf_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [322]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [323]:
scores

array([0.51666667, 0.525     , 0.575     , 0.425     ])

In [324]:
mean_score

0.5104166666666666

In [325]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [326]:
scores

array([0.55      , 0.575     , 0.49166667, 0.575     ])

In [327]:
mean_score

0.5479166666666666

In [328]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [329]:
scores

array([0.53333333, 0.51666667, 0.53333333, 0.56666667, 0.55      ,
       0.53333333, 0.5       , 0.51666667])

In [330]:
mean_score

0.53125

In [331]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [332]:
scores

array([0.53333333, 0.53333333, 0.51666667, 0.53333333, 0.58333333,
       0.43333333, 0.55      , 0.6       ])

In [333]:
mean_score

0.5354166666666667

In [334]:
# other metrics + graphs




### Hyper_optimized Model

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [335]:
hm_rf_to = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [336]:
hm_rf_to.fit()

Initial Model with Stock Params Score : 0.5270833333333333
Fitting 4 folds for each of 300 candidates, totalling 1200 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed: 45.1min finished


Random HP Search Best Model Score : 0.5375000000000001
Improvement of 1.976284584980251% relative to the initial model


In [337]:
hm_rf_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [338]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [339]:
scores

array([0.54166667, 0.5       , 0.58333333, 0.48333333])

In [340]:
mean_score

0.5270833333333333

In [341]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [342]:
scores

array([0.59166667, 0.525     , 0.55833333, 0.56666667])

In [343]:
mean_score

0.5604166666666667

In [344]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [345]:
scores

array([0.53333333, 0.48333333, 0.46666667, 0.55      , 0.55      ,
       0.53333333, 0.55      , 0.5       ])

In [346]:
mean_score

0.5208333333333334

In [347]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [348]:
scores

array([0.51666667, 0.55      , 0.51666667, 0.53333333, 0.6       ,
       0.45      , 0.53333333, 0.6       ])

In [349]:
mean_score

0.5375000000000001

In [350]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [351]:
hm_rf_tos = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [352]:
hm_rf_tos.fit()

Initial Model with Stock Params Score : 0.5479166666666667
Fitting 4 folds for each of 300 candidates, totalling 1200 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed: 41.3min finished


Random HP Search Best Model Score : 0.5854166666666666
Improvement of 6.844106463878302% relative to the initial model


In [353]:
hm_rf_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [354]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [355]:
scores

array([0.55      , 0.48333333, 0.6       , 0.45833333])

In [356]:
mean_score

0.5229166666666667

In [357]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [358]:
scores

array([0.575     , 0.59166667, 0.575     , 0.58333333])

In [359]:
mean_score

0.5812499999999999

In [360]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [361]:
scores

array([0.51666667, 0.45      , 0.45      , 0.53333333, 0.58333333,
       0.56666667, 0.51666667, 0.45      ])

In [362]:
mean_score

0.5083333333333333

In [363]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [364]:
scores

array([0.5       , 0.55      , 0.48333333, 0.56666667, 0.61666667,
       0.43333333, 0.51666667, 0.6       ])

In [365]:
mean_score

0.5333333333333334

In [366]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [367]:
hm_rf_ro = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [368]:
hm_rf_ro.fit()

Initial Model with Stock Params Score : 0.50625
Fitting 8 folds for each of 300 candidates, totalling 2400 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed: 92.1min finished


Random HP Search Best Model Score : 0.5354166666666667
Improvement of 5.761316872427985% relative to the initial model


In [369]:
hm_rf_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [370]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [371]:
scores

array([0.5       , 0.51666667, 0.59166667, 0.51666667])

In [372]:
mean_score

0.53125

In [373]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [374]:
scores

array([0.53333333, 0.53333333, 0.56666667, 0.55833333])

In [375]:
mean_score

0.5479166666666666

In [376]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [377]:
scores

array([0.5       , 0.53333333, 0.5       , 0.56666667, 0.55      ,
       0.51666667, 0.5       , 0.48333333])

In [378]:
mean_score

0.51875

In [379]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [380]:
scores

array([0.51666667, 0.53333333, 0.4       , 0.48333333, 0.63333333,
       0.38333333, 0.48333333, 0.56666667])

In [381]:
mean_score

0.5

In [382]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [383]:
hm_rf_ros = hyper_model(model_name='random_forest_classifier',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [384]:
hm_rf_ros.fit()

Initial Model with Stock Params Score : 0.5229166666666667
Fitting 8 folds for each of 300 candidates, totalling 2400 fits


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed: 98.2min finished


Random HP Search Best Model Score : 0.5479166666666667
Improvement of 4.780876494023908% relative to the initial model


In [385]:
hm_rf_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [386]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



In [387]:
scores

array([0.53333333, 0.49166667, 0.58333333, 0.48333333])

In [388]:
mean_score

0.5229166666666667

In [389]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_rf_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [390]:
scores

array([0.56666667, 0.58333333, 0.55      , 0.59166667])

In [391]:
mean_score

0.5729166666666666

In [392]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_rf_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [393]:
scores

array([0.51666667, 0.46666667, 0.45      , 0.51666667, 0.58333333,
       0.56666667, 0.46666667, 0.48333333])

In [394]:
mean_score

0.50625

In [395]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_rf_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


In [396]:
scores

array([0.48333333, 0.53333333, 0.5       , 0.58333333, 0.61666667,
       0.48333333, 0.53333333, 0.6       ])

In [397]:
mean_score

0.5416666666666667

In [398]:
# other metrics + graphs




## XGBoost Classifier

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [399]:
hm_xgb_to = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [400]:
hm_xgb_to.fit()

[02:21:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:21:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:21:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:21:24] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[02:21:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:21:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:21:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:21:25] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:21:27] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:21:27] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:21:27] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:21:27] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:21:29] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:21:29] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:21:29] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:21:29] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[02:22:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:22:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:22:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:22:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed:  1.4min finished


In [401]:
hm_xgb_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [402]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[02:22:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [403]:
scores

array([0.525     , 0.475     , 0.56666667, 0.53333333])

In [404]:
mean_score

0.525

In [405]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:22:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [406]:
scores

array([0.51666667, 0.55833333, 0.55      , 0.61666667])

In [407]:
mean_score

0.5604166666666668

In [408]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:22:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [409]:
scores

array([0.43333333, 0.51666667, 0.46666667, 0.55      , 0.61666667,
       0.53333333, 0.5       , 0.53333333])

In [410]:
mean_score

0.51875

In [411]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_to.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:22:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [412]:
scores

array([0.5       , 0.58333333, 0.56666667, 0.5       , 0.58333333,
       0.46666667, 0.5       , 0.66666667])

In [413]:
mean_score

0.5458333333333334

In [414]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [415]:
hm_xgb_tos = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [416]:
hm_xgb_tos.fit()

[02:22:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[02:22:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:22:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:22:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:22:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[02:24:09] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:09] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:09] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:09] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:24:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:11] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:24:12] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:12] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:12] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:13] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:24:14] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:14] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:14] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:14] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed:  1.4min finished


In [417]:
hm_xgb_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [418]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[02:24:14] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:14] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:14] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [419]:
scores

array([0.525     , 0.475     , 0.56666667, 0.53333333])

In [420]:
mean_score

0.525

In [421]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:24:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [422]:
scores

array([0.51666667, 0.55833333, 0.55      , 0.61666667])

In [423]:
mean_score

0.5604166666666668

In [424]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:24:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:15] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [425]:
scores

array([0.43333333, 0.51666667, 0.46666667, 0.55      , 0.61666667,
       0.53333333, 0.5       , 0.53333333])

In [426]:
mean_score

0.51875

In [427]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_tos.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:24:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [428]:
scores

array([0.5       , 0.58333333, 0.56666667, 0.5       , 0.58333333,
       0.46666667, 0.5       , 0.66666667])

In [429]:
mean_score

0.5458333333333334

In [430]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [431]:
hm_xgb_ro = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [432]:
hm_xgb_ro.fit()

[02:24:16] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:17] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:17] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:17] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[02:24:17] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:18] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:18] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:18] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:24:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:20] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:24:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:24:22] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[02:26:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:36] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:37] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:37] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:26:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:38] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:26:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:39] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:26:40] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:40] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:41] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:41] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed:  2.4min finished


In [433]:
hm_xgb_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [434]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[02:26:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [435]:
scores

array([0.525     , 0.475     , 0.56666667, 0.53333333])

In [436]:
mean_score

0.525

In [437]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:26:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [438]:
scores

array([0.51666667, 0.55833333, 0.55      , 0.61666667])

In [439]:
mean_score

0.5604166666666668

In [440]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:26:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:42] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [441]:
scores

array([0.43333333, 0.51666667, 0.46666667, 0.55      , 0.61666667,
       0.53333333, 0.5       , 0.53333333])

In [442]:
mean_score

0.51875

In [443]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_ro.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:26:43] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:43] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:43] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:43] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [444]:
scores

array([0.5       , 0.58333333, 0.56666667, 0.5       , 0.58333333,
       0.46666667, 0.5       , 0.66666667])

In [445]:
mean_score

0.5458333333333334

In [446]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [447]:
hm_xgb_ros = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [448]:
hm_xgb_ros.fit()

[02:26:43] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[02:26:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:26:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:26:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:26:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[02:28:43] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:43] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:43] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:43] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:28:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:44] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:45] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:28:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:46] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:28:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed:  2.1min finished


In [449]:
hm_xgb_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [450]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[02:28:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [451]:
scores

array([0.525     , 0.475     , 0.56666667, 0.53333333])

In [452]:
mean_score

0.525

In [453]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:28:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [454]:
scores

array([0.51666667, 0.55833333, 0.55      , 0.61666667])

In [455]:
mean_score

0.5604166666666668

In [456]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:28:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [457]:
scores

array([0.43333333, 0.51666667, 0.46666667, 0.55      , 0.61666667,
       0.53333333, 0.5       , 0.53333333])

In [458]:
mean_score

0.51875

In [459]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_ros.stock_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:28:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [460]:
scores

array([0.5       , 0.58333333, 0.56666667, 0.5       , 0.58333333,
       0.46666667, 0.5       , 0.66666667])

In [461]:
mean_score

0.5458333333333334

In [462]:
# other metrics + graphs




### Hyper_optimized model

### Stock Model

#### *leave-one-task-out* cross validation

##### Training

In [463]:
hm_xgb_to = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-task-out',
                            X=X,
                            y=y)

In [464]:
hm_xgb_to.fit()

[02:28:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[02:28:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:28:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:28:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:28:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[02:29:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:47] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:29:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:29:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

Random HP Search Best Model Score : 0.53125
Improvement of 1.1904761904761862% relative to the initial model


[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed:   59.7s finished


In [465]:
hm_xgb_to.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [466]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[02:29:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [467]:
scores

array([0.5       , 0.53333333, 0.55      , 0.54166667])

In [468]:
mean_score

0.53125

In [469]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:29:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [470]:
scores

array([0.55      , 0.51666667, 0.55      , 0.55833333])

In [471]:
mean_score

0.5437500000000001

In [472]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:29:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [473]:
scores

array([0.48333333, 0.48333333, 0.36666667, 0.6       , 0.56666667,
       0.51666667, 0.51666667, 0.51666667])

In [474]:
mean_score

0.5062500000000001

In [475]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_to.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:29:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [476]:
scores

array([0.55      , 0.56666667, 0.46666667, 0.5       , 0.6       ,
       0.48333333, 0.48333333, 0.66666667])

In [477]:
mean_score

0.5395833333333333

In [478]:
# other metrics + graphs




#### *leave-one-task-out-shuffled* cross validation

##### Training

In [479]:
hm_xgb_tos = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-task-out-shuffled',
                            X=X,
                            y=y)

In [480]:
hm_xgb_tos.fit()

[02:29:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[02:29:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:29:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:29:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:29:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[02:30:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:49] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:50] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:30:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:51] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:30:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:52] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:30:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:53] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 1200 out of 1200 | elapsed:  1.0min finished


In [481]:
hm_xgb_tos.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [482]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[02:30:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [483]:
scores

array([0.51666667, 0.45833333, 0.56666667, 0.46666667])

In [484]:
mean_score

0.5020833333333333

In [485]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:30:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [486]:
scores

array([0.58333333, 0.60833333, 0.54166667, 0.575     ])

In [487]:
mean_score

0.5770833333333334

In [488]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:30:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:54] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [489]:
scores

array([0.53333333, 0.5       , 0.45      , 0.51666667, 0.53333333,
       0.56666667, 0.46666667, 0.53333333])

In [490]:
mean_score

0.5125

In [491]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_tos.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:30:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [492]:
scores

array([0.48333333, 0.55      , 0.51666667, 0.55      , 0.6       ,
       0.43333333, 0.5       , 0.6       ])

In [493]:
mean_score

0.5291666666666668

In [494]:
# other metrics + graphs




#### *leave-one-run-out* cross validation

##### Training

In [495]:
hm_xgb_ro = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-run-out',
                            X=X,
                            y=y)

In [496]:
hm_xgb_ro.fit()

[02:30:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:55] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.



[02:30:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_re

[02:30:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:30:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:30:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[02:32:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:32:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:32:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:32:56] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:32:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:32:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:32:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:32:57] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:32:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:32:58] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:32:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:32:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:33:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
Random HP Search Best Model Score : 0.55
Improvement of 6.024096385542168% relative to the initial model


[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed:  2.1min finished


In [497]:
hm_xgb_ro.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [498]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[02:33:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [499]:
scores

array([0.48333333, 0.525     , 0.525     , 0.475     ])

In [500]:
mean_score

0.5020833333333333

In [501]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:33:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:00] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [502]:
scores

array([0.54166667, 0.56666667, 0.54166667, 0.60833333])

In [503]:
mean_score

0.5645833333333333

In [504]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:33:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [505]:
scores

array([0.56666667, 0.5       , 0.5       , 0.6       , 0.55      ,
       0.56666667, 0.56666667, 0.55      ])

In [506]:
mean_score

0.55

In [507]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_ro.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:33:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [508]:
scores

array([0.48333333, 0.56666667, 0.56666667, 0.48333333, 0.63333333,
       0.5       , 0.48333333, 0.6       ])

In [509]:
mean_score

0.5395833333333333

In [510]:
# other metrics + graphs




#### *leave-one-run-out-shuffled* cross validation

##### Training

In [511]:
hm_xgb_ros = hyper_model(model_name='xg_boost',
                            validation_approach = 'leave-one-run-out-shuffled',
                            X=X,
                            y=y)

In [512]:
hm_xgb_ros.fit()

[02:33:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.



[02:33:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_re

[02:33:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:33:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:33:06] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

...

[02:34:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:34:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:34:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:34:59] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:35:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:01] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:35:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:02] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[02:35:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:03] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

[Parallel(n_jobs=1)]: Done 2400 out of 2400 | elapsed:  2.0min finished


In [513]:
hm_xgb_ros.all_models_perf

Empty DataFrame
Columns: [Model Iteration, Score]
Index: []

##### Test

In [514]:
# leave-one-task-out test
cv = KFold(n_splits=4,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)



[02:35:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [515]:
scores

array([0.48333333, 0.48333333, 0.575     , 0.50833333])

In [516]:
mean_score

0.5125

In [517]:
# leave-one-task-out-shuffed test
cv = KFold(n_splits=4,shuffle=True,random_state=42)

scores = cross_val_score(estimator=hm_xgb_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:35:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [518]:
scores

array([0.55      , 0.50833333, 0.56666667, 0.6       ])

In [519]:
mean_score

0.55625

In [520]:
# leave-one-run-out test
cv = KFold(n_splits=8,shuffle=False)

scores = cross_val_score(estimator=hm_xgb_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:35:04] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [521]:
scores

array([0.46666667, 0.46666667, 0.48333333, 0.58333333, 0.53333333,
       0.6       , 0.56666667, 0.51666667])

In [522]:
mean_score

0.5270833333333333

In [523]:
# leave-one-run-out-shuffed test
cv = KFold(n_splits=8,shuffle=True,random_state=42)



scores = cross_val_score(estimator=hm_xgb_ros.rd_model,cv=cv,X=X,y=y)

mean_score = np.mean(scores)


[02:35:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_release_1.3.0/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[02:35:05] WARNING: C:/Users/Administrator/workspace/xgboost-win64_rel

In [524]:
scores

array([0.58333333, 0.56666667, 0.55      , 0.46666667, 0.6       ,
       0.5       , 0.51666667, 0.65      ])

In [525]:
mean_score

0.5541666666666667

In [526]:
# other metrics + graphs


